In [1]:
from ssd import build_ssd
from layers.box_utils import *
import os
import sys
import torch
from torch.autograd import Variable
import torch.nn as nn
import torch.optim as optim
import torch.backends.cudnn as cudnn
import torch.nn.init as init
import torch.utils.data as data
import numpy as np
import argparse
import torchvision
import pickle
from layers import box_utils
from layers import Detect
from layers import functions
from layers import modules
import torch.nn.functional as F
from math import sqrt as sqrt
from itertools import product as product

from torch.autograd import Function
from layers.box_utils import decode, nms

In [2]:
## 詳細模型結構可以參考ssd.py
ssd_net=build_ssd('train', size=300, num_classes=21)
ssd_net.load_weights('./demo/ssd300_mAP_77.43_v2.pth')

C:\Python\GitHub\TEMP_1st-DL-CVMarathon\data\ssd.py:34: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.
  self.priors = Variable(self.priorbox.forward(), volatile=True)


Loading weights into state dict...
Finished!


## 默認Config檔案在data/config.py內

In [3]:
ssd_net.cfg

{'num_classes': 21,
 'lr_steps': (80000, 100000, 120000),
 'max_iter': 120000,
 'feature_maps': [38, 19, 10, 5, 3, 1],
 'min_dim': 300,
 'steps': [8, 16, 32, 64, 100, 300],
 'min_sizes': [30, 60, 111, 162, 213, 264],
 'max_sizes': [60, 111, 162, 213, 264, 315],
 'aspect_ratios': [[2], [2, 3], [2, 3], [2, 3], [2], [2]],
 'variance': [0.1, 0.2],
 'clip': True,
 'name': 'VOC'}

In [4]:
cfg = {
    'num_classes': 21,
    'lr_steps': (80000, 100000, 120000),
    'max_iter': 120000,
    'feature_maps': [38, 19, 10, 5, 3, 1],
    'min_dim': 300,
    'steps': [8, 16, 32, 64, 100, 300],
    'min_sizes': [30, 60, 111, 162, 213, 264],
    'max_sizes': [60, 111, 162, 213, 264, 315],
    'aspect_ratios': [[2], [2, 3], [2, 3], [2, 3], [2], [2]],
    'variance': [0.1, 0.2],
    'clip': True,
    'name': 'VOC',
}

### 'aspect_ratios' : 使用六張Feature Map，每一張上方有預設的anchor boxes，Boxes aspect ratio可以自己設定
### 'feature_maps' : 使用feature map大小為[38x38, 19x19, 10x10, 5x5, 3x3, 1x1]
### 'min_sizes'、'max_sizes'可藉由下方算式算出，由作者自行設計
### 'steps' : Feature map回放回原本300*300的比例，如38要回放為300大概就是8倍
### 'variance' : Training 的一個trick，加速收斂，詳見：https://github.com/rykov8/ssd_keras/issues/53

---

## 'min_sizes'、'max_sizes' 計算

In [5]:
import math
## source:https://blog.csdn.net/gbyy42299/article/details/81235891
min_dim = 300   ## 维度
# conv4_3 ==> 38 x 38
# fc7 ==> 19 x 19
# conv6_2 ==> 10 x 10
# conv7_2 ==> 5 x 5
# conv8_2 ==> 3 x 3
# conv9_2 ==> 1 x 1
mbox_source_layers = ['conv4_3', 'fc7', 'conv6_2', 'conv7_2', 'conv8_2', 'conv9_2'] ## prior_box來源層，可以更改。很多改進都是基於此處的調整。
# in percent %
min_ratio = 20 ## 這裡即是論文中所說的Smin的= 0.2，Smax的= 0.9的初始值，經過下面的運算即可得到min_sizes，max_sizes。
max_ratio = 90
step = int(math.floor((max_ratio - min_ratio) / (len(mbox_source_layers) - 2)))## 取一個間距步長，即在下面用於循環給比取值時起一個間距作用。可以用一個具體的數值代替，這裡等於17。
min_sizes = []  ## 經過以下運算得到min_sizes和max_sizes。
max_sizes = []
for ratio in range(min_ratio, max_ratio + 1, step):
    ## 從min_ratio至max_ratio + 1每隔步驟= 17取一個值賦值給比。注意範圍函數的作用。
    ## min_sizes.append（）函數即把括號內部每次得到的值依次給了min_sizes。
    min_sizes.append(min_dim * ratio / 100.)
    max_sizes.append(min_dim * (ratio + step) / 100.)
min_sizes = [min_dim * 10 / 100.] + min_sizes
max_sizes = [min_dim * 20 / 100.] + max_sizes

## steps: 這一步要仔細理解，即計算卷積層產生的prior_box距離原圖的步長，先驗框中心點的坐標會乘以step，
## 相當於從特徵映射位置映射回原圖位置，比如conv4_3輸出特徵圖大小為38 *38，而輸入的圖片為300* 300，
## 所以38 *8約等於300，所以映射步長為8.這是針對300* 300的訓練圖片。
steps = [8, 16, 32, 64, 100, 300]  
aspect_ratios = [[2], [2, 3], [2, 3], [2, 3], [2], [2]]
 
print('min_sizes: ',min_sizes)
print('max_sizes: ',max_sizes)


min_sizes:  [30.0, 60.0, 111.0, 162.0, 213.0, 264.0]
max_sizes:  [60.0, 111.0, 162.0, 213.0, 264.0, 315.0]


---

## Default anchor boxes設計原理，看懂收穫很多
##### 可以理解 SSD原文中 8732個anchors是怎麼來的
##### 38×38×4+19×19×6+10×10×6+5×5×6+3×3×4+1×1×4=8732

In [6]:
class PriorBox(object):
    """Compute priorbox coordinates in center-offset form for each source
    feature map.
    """
    def __init__(self, cfg):
        super(PriorBox, self).__init__()
        self.image_size = cfg['min_dim']
        # number of priors for feature map location (either 4 or 6)
        self.num_priors = len(cfg['aspect_ratios'])
        self.variance = cfg['variance'] or [0.1]
        self.feature_maps = cfg['feature_maps']
        self.min_sizes = cfg['min_sizes']
        self.max_sizes = cfg['max_sizes']
        self.steps = cfg['steps']
        self.aspect_ratios = cfg['aspect_ratios']
        self.clip = cfg['clip']
        self.version = cfg['name']
        for v in self.variance:
            if v <= 0:
                raise ValueError('Variances must be greater than 0')

    def forward(self):
        mean = []
        '''依照Feature map大小找出所有的pixel 中心'''
        '''下方這兩個loop會找出W個x軸pixel對上W個y軸pixel，假如現在是在38x38的feature map上，就會有38x38個值'''
        '''ex. [0,1],[0,2]..[0,37] [1,1],[1,2]..[1,37]..........[37,37]'''
        for k, f in enumerate(self.feature_maps):
            for i, j in product(range(f), repeat=2):
                f_k = self.image_size / self.steps[k] ## 如self.steps==8，就是先將原圖size normalize(/300)後再乘上8
                # unit center x,y
                '''中心點'''
                cx = (j + 0.5) / f_k
                cy = (i + 0.5) / f_k

                # aspect_ratio: 1
                # rel size: min_size
                '''/self.image_size 就是在做normalization '''
                s_k = self.min_sizes[k]/self.image_size
                '''小的正方形box'''
                mean += [cx, cy, s_k, s_k]

                # aspect_ratio: 1
                # rel size: sqrt(s_k * s_(k+1))
                '''大的正方形box'''
                s_k_prime = sqrt(s_k * (self.max_sizes[k]/self.image_size))
                mean += [cx, cy, s_k_prime, s_k_prime]

                # rest of aspect ratios
                for ar in self.aspect_ratios[k]:
                    '''aspect ratio 2,3'''
                    mean += [cx, cy, s_k*sqrt(ar), s_k/sqrt(ar)]
                    '''aspect ratio 1/2,1/3'''
                    mean += [cx, cy, s_k/sqrt(ar), s_k*sqrt(ar)]
        # back to torch land
        output = torch.Tensor(mean).view(-1, 4)
        if self.clip:
            output.clamp_(max=1, min=0)
        return output

In [7]:
PriorBox_Demo=PriorBox(cfg)

In [8]:
print(PriorBox_Demo.forward().shape)

torch.Size([8732, 4])


---

## Loss 如何設計

In [9]:
class MultiBoxLoss(nn.Module):

    def __init__(self, num_classes, overlap_thresh, prior_for_matching,
                 bkg_label, neg_mining, neg_pos, neg_overlap, encode_target,
                 use_gpu=True):
        super(MultiBoxLoss, self).__init__()
        self.use_gpu = use_gpu
        '''有幾類'''
        self.num_classes = num_classes
        '''判定為正樣本的threshold，一般設為0.5'''
        self.threshold = overlap_thresh
        '''background自己會有一類，不用Label，假如我們有20類一樣標註0-19，下方會自己空出一類給background'''
        self.background_label = bkg_label
        self.encode_target = encode_target
        self.use_prior_for_matching = prior_for_matching
        '''OHEM，找出分得最不好的樣品，也就是confidence score比較低的正負樣品'''
        self.do_neg_mining = neg_mining
        '''負樣品與正樣品的比例，通常是3:1'''
        self.negpos_ratio = neg_pos
        self.neg_overlap = neg_overlap
        self.variance = cfg['variance']
     

    def forward(self, predictions, targets):

        '''prediction會output三個值'''
        '''loc shape: bounding box 資訊，torch.size(batch_size,num_priors,4)'''
        '''conf shape: 每一個bounding box 的信心程度，torch.size(batch_size,num_priors,num_classes)'''
        '''priors shape: 預設的defaul box， torch.size(num_priors,4)'''
        loc_data, conf_data, priors = predictions
        num = loc_data.size(0)
        priors = priors[:loc_data.size(1), :]
        num_priors = (priors.size(0))
        num_classes = self.num_classes

        # match priors (default boxes) and ground truth boxes
        loc_t = torch.Tensor(num, num_priors, 4)
        conf_t = torch.LongTensor(num, num_priors)
        for idx in range(num):
            truths = targets[idx][:, :-1].data
            labels = targets[idx][:, -1].data
            defaults = priors.data
            '''jaccard 計算每一個BBOX與ground truth的IOU'''
            match(self.threshold, truths, defaults, self.variance, labels,
                  loc_t, conf_t, idx)
        if self.use_gpu:
            loc_t = loc_t.cuda()
            conf_t = conf_t.cuda()
        '''用Variable包裝'''
        loc_t = Variable(loc_t, requires_grad=False)
        conf_t = Variable(conf_t, requires_grad=False)

        pos = conf_t > 0
        num_pos = pos.sum(dim=1, keepdim=True)


        pos_idx = pos.unsqueeze(pos.dim()).expand_as(loc_data)
        loc_p = loc_data[pos_idx].view(-1, 4)
        loc_t = loc_t[pos_idx].view(-1, 4)
        '''smooth_l1_loss 計算bounding box regression'''
        loss_l = F.smooth_l1_loss(loc_p, loc_t, size_average=False)

        # Compute max conf across batch for hard negative mining
        batch_conf = conf_data.view(-1, self.num_classes)
        loss_c = log_sum_exp(batch_conf) - batch_conf.gather(1, conf_t.view(-1, 1))

        # Hard Negative Mining
        loss_c = loss_c.view(num, -1)
        loss_c[pos] = 0
        '''排列confidence 的分數'''
        _, loss_idx = loss_c.sort(1, descending=True)
        _, idx_rank = loss_idx.sort(1)
        num_pos = pos.long().sum(1, keepdim=True)
        '''負樣品取出數量 == negpos_ratio*num_pos'''
        num_neg = torch.clamp(self.negpos_ratio*num_pos, max=pos.size(1)-1)
        neg = idx_rank < num_neg.expand_as(idx_rank)

        # Confidence Loss Including Positive and Negative Examples
        pos_idx = pos.unsqueeze(2).expand_as(conf_data)
        neg_idx = neg.unsqueeze(2).expand_as(conf_data)
        conf_p = conf_data[(pos_idx+neg_idx).gt(0)].view(-1, self.num_classes)
        targets_weighted = conf_t[(pos+neg).gt(0)]
        '''用cross_entropy做分類'''
        loss_c = F.cross_entropy(conf_p, targets_weighted, size_average=False)

        # Sum of losses: L(x,c,l,g) = (Lconf(x, c) + αLloc(x,l,g)) / N
        #double轉成torch.float64
        N = num_pos.data.sum().double()
        loss_l = loss_l.double()
        loss_c = loss_c.double()
        loss_l /= N
        loss_c /= N
        return loss_l, loss_c


## 產生我們Loss function，注意這裡的class要包含背景

In [10]:
Use_cuda=True
criterion = MultiBoxLoss(21, 0.5, True, 0, False, 3, 0.5,False, Use_cuda,)

----

## 基本設定

In [11]:
ssd_net=build_ssd('train', size=300, num_classes=21)
use_pretrained=True
if use_pretrained:
    ssd_net.load_weights('./demo/ssd300_mAP_77.43_v2.pth')
net=ssd_net

Loading weights into state dict...
Finished!


In [17]:

'''要不要使用gpu'''
Use_cuda=False

torch.set_default_tensor_type('torch.FloatTensor')    
'''tensor type會依照cpu或gpu有所不同'''
#if torch.cuda.is_available():
#    if args.cuda:
#        torch.set_default_tensor_type('torch.cuda.FloatTensor')
#    if not args.cuda:
#        print("WARNING: It looks like you have a CUDA device, but aren't " +
#              "using CUDA.\nRun with --cuda for optimal training speed.")
#        torch.set_default_tensor_type('torch.FloatTensor')
#else:
#    torch.set_default_tensor_type('torch.FloatTensor')

'''使用GPU時可以開啟DataParallel，但當Input是不定大小時，要關掉'''
if Use_cuda:
    net = torch.nn.DataParallel(ssd_net)
    cudnn.benchmark = True
'''使用GPU時模型要轉成cuda'''
if Use_cuda:
    net = net.cuda()
    
batch_size_=1
optimizer = optim.Adam(net.parameters(),lr=0.00001/batch_size_)

---

## 訓練

## 這裡我們先示範輸入的 image,Label格式，真正在訓練時，準備成一樣格式即可

In [18]:
'''輸入影像格式，假設batch size 為 4'''
image_in=torch.tensor(torch.rand(4,3,300,300),dtype=torch.float32)
'''Label格式，沒有固定長度，看圖像中有幾個label就有幾個'''
label_0=[[ 0.1804,  0.6076,  0.7701,  0.8485, 0.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 3.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 19.0000],
       [ 0.2950,  0.0000,  0.8238,  0.3641, 6.0000],]
label_1=[[ 0.1804,  0.6076,  0.7701,  0.8485, 13.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 11.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 7.0000],
       [ 0.2950,  0.0000,  0.8238,  0.3641, 5.0000],]
label_2=[[ 0.1804,  0.6076,  0.7701,  0.8485, 0.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 3.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 14.0000],
       [ 0.2950,  0.0000,  0.8238,  0.3641, 6.0000],]
label_3=[[ 0.1804,  0.6076,  0.7701,  0.8485, 0.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 3.0000],
       [ 0.2250,  0.0000,  0.9238,  0.5641, 19.0000],
       [ 0.2950,  0.0000,  0.8238,  0.3641, 6.0000],]

C:\Users\wjr63\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  


In [19]:
epochs=300
iteration=1000

In [20]:
for epoch in range(epochs):
    n=0
    loss_sum=[]
    loc_loss=[]
    conf_loss=[]
    for number__ in range(iteration) :
        '''要用Variable包裝tensor才能送入模型'''
        if Use_cuda:
            image_ = Variable(image_in.cuda())
            y = [Variable(torch.tensor(label_0).cuda(), volatile=True),Variable(torch.tensor(label_1).cuda(), 
                volatile=True),Variable(torch.tensor(label_2).cuda(), volatile=True),Variable(torch.tensor(label_3).cuda(), volatile=True)]      
        else:
            image_ = Variable(image_in)
            y = [Variable(torch.tensor(label_0), volatile=True),Variable(torch.tensor(label_1), 
                volatile=True),Variable(torch.tensor(label_2), volatile=True),Variable(torch.tensor(label_3), volatile=True)]

        '''Forward Pass'''
        out = net(image_)
        '''Regression Loss and Classification Loss'''
        loss_l,loss_c = criterion(out,y )
        loss = loss_l+ loss_c
        '''Backward'''
        loss.backward()

        loc_loss.append(loss_l.data.cpu().numpy())
        conf_loss.append(loss_c.data.cpu().numpy())
        loss_sum.append(loss.data.cpu().numpy())
        '''更新參數'''
        optimizer.step()
        '''清空Gradients'''
        optimizer.zero_grad()
        
        n+=1
        if n%10==0:
            print('epochs', epoch,'，iteration', n)
            print('BBOX Regression Loss: ', np.mean(loc_loss))
            print('Classification Loss: ', np.mean(conf_loss))
    '''儲存權重'''
    torch.save(ssd_net.state_dict(),'weights/Weights.pth')

C:\Users\wjr63\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.
  
C:\Users\wjr63\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.
  from ipykernel import kernelapp as app
C:\Users\wjr63\Anaconda3\lib\site-packages\torch\nn\_reduction.py:43: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


epochs 0 ，iteration 10
BBOX Regression Loss:  1.9553276909722221
Classification Loss:  7.736771590621382
epochs 0 ，iteration 20
BBOX Regression Loss:  1.7519755681355793
Classification Loss:  5.9395630306667755
epochs 0 ，iteration 30
BBOX Regression Loss:  1.6231179602352193
Classification Loss:  5.063359135757256
epochs 0 ，iteration 40
BBOX Regression Loss:  1.4826258111883093
Classification Loss:  4.4940866117124205
epochs 0 ，iteration 50
BBOX Regression Loss:  1.3436099596376776
Classification Loss:  4.059271497373228
epochs 0 ，iteration 60
BBOX Regression Loss:  1.213782998073248
Classification Loss:  3.7008991170812537
epochs 0 ，iteration 70
BBOX Regression Loss:  1.0970678021668128
Classification Loss:  3.3878189430034977
epochs 0 ，iteration 80
BBOX Regression Loss:  0.9909006149680526
Classification Loss:  3.110721793881169
epochs 0 ，iteration 90
BBOX Regression Loss:  0.8967383871353211
Classification Loss:  2.863162384504153
epochs 0 ，iteration 100
BBOX Regression Loss:  0.817

BBOX Regression Loss:  0.10971516337815433
Classification Loss:  0.35987865477585346
epochs 0 ，iteration 780
BBOX Regression Loss:  0.10830865564073704
Classification Loss:  0.35526946409475424
epochs 0 ，iteration 790
BBOX Regression Loss:  0.1069377352271009
Classification Loss:  0.3507767354721091
epochs 0 ，iteration 800
BBOX Regression Loss:  0.10560107545377023
Classification Loss:  0.34639612416426346
epochs 0 ，iteration 810
BBOX Regression Loss:  0.10429741322812475
Classification Loss:  0.3421234967014154
epochs 0 ，iteration 820
BBOX Regression Loss:  0.10302554256039925
Classification Loss:  0.33795491547442397
epochs 0 ，iteration 830
BBOX Regression Loss:  0.10178431503026161
Classification Loss:  0.33388663457473017
epochs 0 ，iteration 840
BBOX Regression Loss:  0.10057263757447561
Classification Loss:  0.32991508062554414
epochs 0 ，iteration 850
BBOX Regression Loss:  0.09939060971796394
Classification Loss:  0.32603686160251727
epochs 0 ，iteration 860
BBOX Regression Loss: 

BBOX Regression Loss:  0.0003888862594033492
Classification Loss:  0.0001808778268319589
epochs 1 ，iteration 510
BBOX Regression Loss:  0.0003817300930822755
Classification Loss:  0.00018046229493384267
epochs 1 ，iteration 520
BBOX Regression Loss:  0.0003745898854789076
Classification Loss:  0.00017992203731482525
epochs 1 ，iteration 530
BBOX Regression Loss:  0.00036761446775631843
Classification Loss:  0.00017927124481947583
epochs 1 ，iteration 540
BBOX Regression Loss:  0.0003608520495795153
Classification Loss:  0.00017852506846884479
epochs 1 ，iteration 550
BBOX Regression Loss:  0.00035432122597859516
Classification Loss:  0.00017769728445444848
epochs 1 ，iteration 560
BBOX Regression Loss:  0.0003480164361802068
Classification Loss:  0.0001768102879246707
epochs 1 ，iteration 570
BBOX Regression Loss:  0.00034192961451696204
Classification Loss:  0.0001758744454833112
epochs 1 ，iteration 580
BBOX Regression Loss:  0.0003360506085198368
Classification Loss:  0.0001748997285143778

Classification Loss:  0.0011329984825468225
epochs 2 ，iteration 230
BBOX Regression Loss:  0.0001787361941660639
Classification Loss:  0.0010965649824403526
epochs 2 ，iteration 240
BBOX Regression Loss:  0.00017204978158352549
Classification Loss:  0.0010625057014418237
epochs 2 ，iteration 250
BBOX Regression Loss:  0.000167794358080115
Classification Loss:  0.0010306325135407623
epochs 2 ，iteration 260
BBOX Regression Loss:  0.000162505372943147
Classification Loss:  0.0010007189889239452
epochs 2 ，iteration 270
BBOX Regression Loss:  0.00015714103941673435
Classification Loss:  0.0009725798958777074
epochs 2 ，iteration 280
BBOX Regression Loss:  0.0001520304116956328
Classification Loss:  0.0009460472556018324
epochs 2 ，iteration 290
BBOX Regression Loss:  0.00014944795129873036
Classification Loss:  0.0009209923056045863
epochs 2 ，iteration 300
BBOX Regression Loss:  0.00015047508296211833
Classification Loss:  0.0008973813351289726
epochs 2 ，iteration 310
BBOX Regression Loss:  0.0

...

BBOX Regression Loss:  1.7328147877996236e-05
Classification Loss:  1.4842448974801762e-09
epochs 296 ，iteration 480
BBOX Regression Loss:  1.700552632683216e-05
Classification Loss:  1.4533231287826724e-09
epochs 296 ，iteration 490
BBOX Regression Loss:  1.6673629333364397e-05
Classification Loss:  1.42366347309323e-09
epochs 296 ，iteration 500
BBOX Regression Loss:  1.6346408759571004e-05
Classification Loss:  1.3951902036313656e-09
epochs 296 ，iteration 510
BBOX Regression Loss:  1.602848011623015e-05
Classification Loss:  1.367833532971927e-09
epochs 296 ，iteration 520
BBOX Regression Loss:  1.572873770947566e-05
Classification Loss:  1.6641752672331284e-09
epochs 296 ，iteration 530
BBOX Regression Loss:  1.60472920017136e-05
Classification Loss:  2.415841647080822e-09
epochs 296 ，iteration 540
BBOX Regression Loss:  1.6842855743379355e-05
Classification Loss:  2.501923360942322e-09
epochs 296 ，iteration 550
BBOX Regression Loss:  1.696122278422127e-05
Classification Loss:  2.45643

epochs 297 ，iteration 190
BBOX Regression Loss:  1.2815046182647293e-05
Classification Loss:  2.323767827500609e-10
epochs 297 ，iteration 200
BBOX Regression Loss:  1.2296764592623734e-05
Classification Loss:  3.09061121057581e-10
epochs 297 ，iteration 210
BBOX Regression Loss:  1.6075612694975265e-05
Classification Loss:  2.943439248167438e-10
epochs 297 ，iteration 220
BBOX Regression Loss:  1.7079663730591007e-05
Classification Loss:  2.809646555068918e-10
epochs 297 ，iteration 230
BBOX Regression Loss:  1.6936941337641254e-05
Classification Loss:  2.6874880091963563e-10
epochs 297 ，iteration 240
BBOX Regression Loss:  1.641635177471679e-05
Classification Loss:  2.575509342146508e-10
epochs 297 ，iteration 250
BBOX Regression Loss:  1.581830760868233e-05
Classification Loss:  2.472488968460648e-10
epochs 297 ，iteration 260
BBOX Regression Loss:  1.5233145881928566e-05
Classification Loss:  2.377393238904469e-10
epochs 297 ，iteration 270
BBOX Regression Loss:  1.4676882940020511e-05
Cl

Classification Loss:  4.663201505523693e-10
epochs 297 ，iteration 900
BBOX Regression Loss:  1.6062817095938846e-05
Classification Loss:  4.905732080279064e-10
epochs 297 ，iteration 910
BBOX Regression Loss:  1.5890967917406522e-05
Classification Loss:  5.531078147655296e-10
epochs 297 ，iteration 920
BBOX Regression Loss:  1.5769499666784196e-05
Classification Loss:  5.66292116223518e-10
epochs 297 ，iteration 930
BBOX Regression Loss:  1.6218283338742686e-05
Classification Loss:  5.791928843168186e-10
epochs 297 ，iteration 940
BBOX Regression Loss:  1.6229519715882055e-05
Classification Loss:  6.106070780772878e-10
epochs 297 ，iteration 950
BBOX Regression Loss:  1.6126417749150408e-05
Classification Loss:  6.041796351501584e-10
epochs 297 ，iteration 960
BBOX Regression Loss:  1.598282166874633e-05
Classification Loss:  6.346790878861039e-10
epochs 297 ，iteration 970
BBOX Regression Loss:  1.582726019195334e-05
Classification Loss:  7.28273628412562e-10
epochs 297 ，iteration 980
BBOX R

epochs 298 ，iteration 610
BBOX Regression Loss:  1.5653795738333804e-05
Classification Loss:  1.143598527566693e-09
epochs 298 ，iteration 620
BBOX Regression Loss:  1.5439412410816586e-05
Classification Loss:  1.1251533900252948e-09
epochs 298 ，iteration 630
BBOX Regression Loss:  1.5208144809231886e-05
Classification Loss:  1.1072938124058457e-09
epochs 298 ，iteration 640
BBOX Regression Loss:  1.4981690293726627e-05
Classification Loss:  1.2003713183932835e-09
epochs 298 ，iteration 650
BBOX Regression Loss:  1.4964667848231234e-05
Classification Loss:  1.1819040673410792e-09
epochs 298 ，iteration 660
BBOX Regression Loss:  1.546001268678223e-05
Classification Loss:  1.1639964299571234e-09
epochs 298 ，iteration 670
BBOX Regression Loss:  1.5503221630602726e-05
Classification Loss:  1.1729825063592626e-09
epochs 298 ，iteration 680
BBOX Regression Loss:  1.5346237043643545e-05
Classification Loss:  1.1557327636186852e-09
epochs 298 ，iteration 690
BBOX Regression Loss:  1.515697565788073

epochs 299 ，iteration 320
BBOX Regression Loss:  1.458834645029083e-05
Classification Loss:  6.512359336570457e-09
epochs 299 ，iteration 330
BBOX Regression Loss:  1.4147518926327805e-05
Classification Loss:  6.31501511425014e-09
epochs 299 ，iteration 340
BBOX Regression Loss:  1.3767547108565756e-05
Classification Loss:  6.129279375595724e-09
epochs 299 ，iteration 350
BBOX Regression Loss:  1.5111695554881086e-05
Classification Loss:  7.266090029761905e-09
epochs 299 ，iteration 360
BBOX Regression Loss:  1.773949764604268e-05
Classification Loss:  7.0642541956018505e-09
epochs 299 ，iteration 370
BBOX Regression Loss:  1.797906523087512e-05
Classification Loss:  6.87332840653153e-09
epochs 299 ，iteration 380
BBOX Regression Loss:  1.7755824170553292e-05
Classification Loss:  6.692451343201753e-09
epochs 299 ，iteration 390
BBOX Regression Loss:  1.738772163442329e-05
Classification Loss:  6.5208500267094e-09
epochs 299 ，iteration 400
BBOX Regression Loss:  1.698365547681575e-05
Classifi